The cell below imports modules used for the code.

In [2]:
!pip install geopandas
!pip install geopy  #needed to install these to get the lat long of missing locations

import pandas as pd
import datetime
from datetime import date
from datetime import datetime, timedelta
import numpy as np
import geopy
import geopandas
from geopy.geocoders import Nominatim
import time

!pip install folium
!conda install -c conda-forge geopy -yes
!conda install -c conda-forge folium=0.5.0 --yes
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import json
import requests
import folium

     |████████████████████████████████| 931kB 7.9MB/s eta 0:00:01
     |████████████████████████████████| 1.8MB 46.9MB/s eta 0:00:01
     |████████████████████████████████| 14.7MB 45.1MB/s eta 0:00:01
     |████████████████████████████████| 10.4MB 45.1MB/s eta 0:00:01
     |████████████████████████████████| 92kB 12.5MB/s eta 0:00:01
usage: conda install [-h] [--revision REVISION] [-y] [--dry-run] [-f]
                     [--file FILE] [--no-deps] [--only-deps] [-m] [-C]
                     [--use-local] [--offline] [--no-pin] [-c CHANNEL]
                     [--override-channels] [-n ENVIRONMENT | -p PATH] [-q]
                     [--copy] [-k] [--update-dependencies]
                     [--no-update-dependencies] [--channel-priority]
                     [--no-channel-priority] [--clobber] [--show-channel-urls]
                     [--no-show-channel-urls] [--download-only] [--json]
                     [--debug] [--verbose]
                     [package_spec [package_spec ...]]


This cell imports the data from the boston hosted site and saves it as inspection_df.  Columns are dropped from this dataframe that are not used further in this project.

In [3]:
inspection_csv_path="https://data.boston.gov/dataset/03693648-2c62-4a2c-a4ec-48de2ee14e18/resource/4582bec6-2b4f-4f9e-bc55-cbaa73117f4c/download/tmpdqyg221v.csv"
inspection_df=pd.read_csv(inspection_csv_path, dtype={'zip':'str'}) #needed to define the zipcode as a string since the mixed frame would drop the first 0 in the zip codes.
inspection_df.drop(columns=['dbaname','descript','licensecat','property_id'], inplace=True) #drops unused columns

The next set of codes creates a new dataframe that is meant to be just a list of the eating establishements.  It deletes duplicate entries so there is one line per business, and all licensea that are listed as "Inactive" (since we don't know why they are inactive or may have been Inactive for a while).  Also additional columns are dropped that are not needed for this list are dropped.  The address is put into a new column that can be read later by geopy to generate missing lat long data.  One location is dropped since the address is not formatted correctly and throws an error later in the code

In [4]:
inspection_list = inspection_df.drop_duplicates('businessname').copy() #drops all repeat listings of businessnames
inspection_list.drop(inspection_list.loc[inspection_list['licstatus']=='Inactive'].index,inplace=True) #drops all lines where license status is inactive
inspection_list.drop(columns=['legalowner','namelast','namefirst','issdttm', 'expdttm','violdttm','result', 'violdesc', 'statusdate','viollevel','violstatus','comments','violation','resultdttm'], inplace=True)
inspection_list['address_zip']= inspection_list['address'] + ', ' + inspection_list['zip']
inspection_list.drop(inspection_list[inspection_list.licenseno == 19320].index, inplace=True)  #this one was dropped since the address was not spelled correctly and didn't export to geocoder
inspection_list.head() #this is the clean dataframe of all business we will add to

businessname  licenseno licstatus               address  \
0        100 Percent Delicia Food      87059    Active   635   Hyde Park AVE   
71      20TH CENTRY BOWLING LANES      18671    Active  1231   Hyde Park AVE   
161  100 Percent Delicias Express     351943    Active       656   Centre ST   
199                149 Eat Street      28288    Active      300   CHELSEA ST   
209        11 Dining - 1St. Floor     413545    Active     200   Berkeley ST   

              city state    zip                       location  \
0       Roslindale    MA  02131  (42.278590000, -71.119440000)   
71       Hyde Park    MA  02136  (42.256820000, -71.124110000)   
161  Jamaica Plain    MA  02130  (42.312830000, -71.113860000)   
199   Charlestown/    MA  02129                            NaN   
209         Boston    MA  02116  (42.350060000, -71.072919000)   

                     address_zip  
0     635   Hyde Park AVE, 02131  
71   1231   Hyde Park AVE, 02136  
161       656   Centre ST, 02130  
199      300   CHELSEA ST, 02129  
209     200   Berkeley ST, 02116

This cell splits the current lat long data (which is a tuple) into two separate new columns "Lat" and "Long"

In [5]:
inspection_list['lat'] = inspection_list['location'].str[1:9].copy()
inspection_list['long'] = inspection_list['location'].str[14:25].copy()
inspection_list.head()

businessname  licenseno licstatus               address  \
0        100 Percent Delicia Food      87059    Active   635   Hyde Park AVE   
71      20TH CENTRY BOWLING LANES      18671    Active  1231   Hyde Park AVE   
161  100 Percent Delicias Express     351943    Active       656   Centre ST   
199                149 Eat Street      28288    Active      300   CHELSEA ST   
209        11 Dining - 1St. Floor     413545    Active     200   Berkeley ST   

              city state    zip                       location  \
0       Roslindale    MA  02131  (42.278590000, -71.119440000)   
71       Hyde Park    MA  02136  (42.256820000, -71.124110000)   
161  Jamaica Plain    MA  02130  (42.312830000, -71.113860000)   
199   Charlestown/    MA  02129                            NaN   
209         Boston    MA  02116  (42.350060000, -71.072919000)   

                     address_zip       lat         long  
0     635   Hyde Park AVE, 02131  42.27859   -71.119440  
71   1231   Hyde Park AVE, 02136  42.25682   -71.124110  
161       656   Centre ST, 02130  42.31283   -71.113860  
199      300   CHELSEA ST, 02129       NaN          NaN  
209     200   Berkeley ST, 02116  42.35006   -71.072919

The next cell runs all of the business in that do not have a lat long code and uses the address in the dataframe to get the lat and long values form geopy.  

In [6]:
inspection_list['location'].fillna(0, inplace=True)  #this takes a while, but fills null locations with 0.
for row_index, row in inspection_list.iterrows():

    if row['location']==0:  #for each row with a 0 in the lat/long, this code looks up the lat long via the address and zip code.
        n=Nominatim(timeout=10, user_agent="Boston-Food").geocode(row['address_zip'])
        #print(n)
        if n!=None:
            location=(n.latitude,n.longitude)
            lat=n.latitude
            long=n.longitude
            #print(row['businessname'])
            inspection_list.loc[row_index,['lat']]=lat #these work
            inspection_list.loc[row_index,['long']]=long #these work
            time.sleep(2) #delays the request so this doesn't get timed out.

inspection_list.tail(10)

businessname  licenseno licstatus  \
596726                     Zen Restaurant     380313    Active   
597396                         Zinneken's     133942    Active   
597606                      ZESTO'S PIZZA      75590    Active   
597680                                 Zo      33151    Active   
597927  Zia Gianna Italian Bakery & Caffe     350090    Active   
597950                 Ziggy's Coffee Bar     154404    Active   
598019                  Zisis Convenience      81039    Active   
598269                    Zuma Restaurant     355979    Active   
598288                           Zo Truck     120456    Active   
598387                Zumas Tex-Mex Grill      26357    Active   

                                 address           city state    zip  \
596726                    21   Beacon ST         Boston    MA  02108   
597396                   1   Citywide ST         Boston    MA  02128   
597606                   460   Centre ST  Jamaica Plain    MA  02130   
597680                3   CENTER PLAZA           BOSTON    MA  02109   
597927              1739  Dorchester AVE     Dorchester    MA  02124   
597950                  100   Tremont ST         Boston    MA  02108   
598019               375   Washington ST       Brighton    MA  02135   
598269                      1  Dalton ST         Boston    MA  02115   
598288                   1   Citywide ST         Boston    MA  02128   
598387  100-199   Faneuil Hall Market PL         Boston    MA  02109   

                             location  \
596726                              0   
597396                              0   
597606  (42.319350000, -71.111540000)   
597680                              0   
597927                              0   
597950  (42.357144000, -71.060857000)   
598019  (42.349318000, -71.154199000)   
598269                              0   
598288                              0   
598387                              0   

                                    address_zip       lat         long  
596726                    21   Beacon ST, 02108   42.4458     -71.0498  
597396                   1   Citywide ST, 02128       NaN          NaN  
597606                   460   Centre ST, 02130  42.31935   -71.111540  
597680                3   CENTER PLAZA  , 02109   42.2933     -71.0639  
597927              1739  Dorchester AVE, 02124   42.2908      -71.063  
597950                  100   Tremont ST, 02108  42.35714   -71.060857  
598019               375   Washington ST, 02135  42.34931   -71.154199  
598269                      1  Dalton ST, 02115   42.3457      -71.084  
598288                   1   Citywide ST, 02128       NaN          NaN  
598387  100-199   Faneuil Hall Market PL, 02109       NaN          NaN

Since the previous step takes a while (1 hr+), the following codes save the output in a dataframe copy such that if I inadvertently delete/change the data, I can reload it without having to wait for all of the missing lat/long values to be populated.

In [7]:
inspection_list_saved=inspection_list.copy() #run once to save the work to the "saved"

In [27]:
inspection_list=inspection_list_saved.copy()  #reload the inspection_list with this.  The copy prevents the reference from indexing.

In [28]:
inspection_list.count()

businessname    3285
licenseno       3285
licstatus       3285
address         3285
city            3285
state           3285
zip             3285
location        3285
address_zip     3285
lat             3050
long            3050
dtype: int64

The collowing code drops all lines with no lat/long data (it was both not provided in the data upload and also it was not able to be generated by geopy using the address and zip code).  Perhaps I can work on this later to add it.

In [29]:
inspection_list.dropna(axis=0, inplace=True) #this drops all entries with NaN in the lat/long, so the resulgting list will all have locations (note, ~235 locations are dropped, and I'll look at this later)
inspection_list.drop(columns=['location', 'address', 'zip'], inplace=True) #drops location, address, and zip since we have these already
inspection_list.tail()

businessname  licenseno licstatus        city  \
597680                                 Zo      33151    Active      BOSTON   
597927  Zia Gianna Italian Bakery & Caffe     350090    Active  Dorchester   
597950                 Ziggy's Coffee Bar     154404    Active      Boston   
598019                  Zisis Convenience      81039    Active    Brighton   
598269                    Zuma Restaurant     355979    Active      Boston   

       state                  address_zip       lat         long  
597680    MA    3   CENTER PLAZA  , 02109   42.2933     -71.0639  
597927    MA  1739  Dorchester AVE, 02124   42.2908      -71.063  
597950    MA      100   Tremont ST, 02108  42.35714   -71.060857  
598019    MA   375   Washington ST, 02135  42.34931   -71.154199  
598269    MA          1  Dalton ST, 02115   42.3457      -71.084

In [30]:
inspection_list.count()

businessname    3050
licenseno       3050
licstatus       3050
city            3050
state           3050
address_zip     3050
lat             3050
long            3050
dtype: int64

From the block above, by dropping restaurants with no lat long data, approximately 235 establishments were removed from the list.

The following creates a temporary dataframe that only has a list of violations that are a failure so it is not counting adminstrative or passes in inspection results.  Also it drops dataframes where the license status is a failure and where the failure is a "HE_Hearing" since this appears to be a failed reinspection of a previous violation and would be like counting the same violation twice.  A new dataframe is then created from this that includes only the inspection results from the past 365 days.  I had created a second dataframe that mirriors the one described above with only "filed" violations.  But later there were so few it didn't seem like a good representation of anything.

In [31]:
inspection_temp=inspection_df.drop(columns=['issdttm','statusdate','expdttm','legalowner','namelast','namefirst'])
inspection_temp.drop(inspection_temp.loc[inspection_temp['violstatus']!='Fail'].index,inplace=True)#drops all values of Pass or NaN, since we don't want to count these
inspection_temp.drop(inspection_temp.loc[inspection_temp['licstatus']=='Inactive'].index,inplace=True) #drops all lines where license status is inactive
inspection_temp.drop(inspection_temp.loc[inspection_temp['result']=='HE_Hearing'].index,inplace=True) #drops all lines where result is HE_Hearing since these are repeats of an original fail.  Maybe something to look into later.


#inspection_temp=inspection_temp.loc[inspection_temp['viollevel']=='**'] #either *, **, ***, or NaN. * seem minor. ** bad, and *** bad, but not as bad as **
#track violdttm within last year and violstatus=Fail.  Add the scaled level of each fail to get a total score.

past_lookback = datetime.today() - timedelta(days=365) #change days to look back for recent violations
inspection_temp['recent_violation']=pd.to_datetime(inspection_temp['violdttm'])>past_lookback #adds column to see if violation was recent.  True is witin the past lookback, false is outside of it.
#inspection_temp.head(100)
inspection_date_filtered=inspection_temp[inspection_temp['recent_violation']==True] #new dataframe with only the recent violations listed in it
#inspection_date_filtered

inspection_date_filtered_filed_only=inspection_date_filtered.drop(inspection_date_filtered.loc[inspection_temp['result']!='HE_Filed'].index) #this is for the FILED only, which is the violations that end up counting against the restaurants score
inspection_date_filtered_filed_only.head(5)

businessname  licenseno licstatus    result  \
148    100 Percent Delicia Food      87059    Active  HE_Filed   
612   20TH CENTRY BOWLING LANES      18671    Active  HE_Filed   
1791                  49 Social      75153    Active  HE_Filed   
2566                75 CHESTNUT      20638    Active  HE_Filed   
2567                75 CHESTNUT      20638    Active  HE_Filed   

               resultdttm           violation viollevel  \
148   2019-05-20 09:04:54         36-6-201.11         *   
612   2019-10-22 11:25:12  590.005/5-203.13-C         *   
1791  2019-10-30 18:16:41  590.006/6-501.11-C         *   
2566  2019-10-15 17:46:13  590.003/3-304.14-C         *   
2567  2019-10-15 17:46:13  590.004/4-602.13-C         *   

                                               violdesc             violdttm  \
148               Floors Designed Constructed Installed  2019-05-20 09:04:54   
612                                    Service Sink (C)  2019-10-22 11:25:12   
1791  Repairing-Premises  Structures  Attachments  a...  2019-10-30 18:16:41   
2566                  Wiping Cloths  Use Limitation (C)  2019-10-15 17:46:13   
2567                       Nonfood Contact Surfaces (C)  2019-10-15 17:46:13   

     violstatus                                           comments  \
148        Fail                regrout floor in kitchen as needed.   
612        Fail                                provide a mop sink.   
1791       Fail  Cardboard lining shelves in walk-in cooler  re...   
2566       Fail  Upon inspection there was no sanitizer set up ...   
2567       Fail  Compressor fan covers interior of walk in refr...   

                   address        city state    zip  \
148    635   Hyde Park AVE  Roslindale    MA  02131   
612   1231   Hyde Park AVE   Hyde Park    MA  02136   
1791         49  Temple Pl      Boston    MA  02111   
2566      75   Chestnut ST      Boston    MA  02108   
2567      75   Chestnut ST      Boston    MA  02108   

                           location  recent_violation  
148   (42.278590000, -71.119440000)              True  
612   (42.256820000, -71.124110000)              True  
1791  (42.354930000, -71.061809000)              True  
2566  (42.356898000, -71.070971000)              True  
2567  (42.356898000, -71.070971000)              True

The following code creates three columns for each of the last-year of violations for each establishment.  The violations are labeled in the data in order of severity (*, **, or ***). 

In [32]:
#violations with all 
violation_list1=inspection_date_filtered.loc[inspection_date_filtered['viollevel']=='*'].groupby(["businessname", "licenseno", "viollevel"]).size().reset_index(name="violations 1") #lists occurances of each violation level for each restaurant
violation_list2=inspection_date_filtered.loc[inspection_date_filtered['viollevel']=='**'].groupby(["businessname","licenseno", "viollevel"]).size().reset_index(name="violations 2")
violation_list3=inspection_date_filtered.loc[inspection_date_filtered['viollevel']=='***'].groupby(["businessname","licenseno", "viollevel"]).size().reset_index(name="violations 3")

violation_list1clean=violation_list1.drop(columns=['viollevel'])
violation_list2clean=violation_list2.drop(columns=['viollevel'])
violation_list3clean=violation_list3.drop(columns=['viollevel'])

violation_list1clean=violation_list1clean.rename(columns={'businessname':'businessname1'})
violation_list2clean=violation_list2clean.rename(columns={'businessname':'businessname2'})
violation_list3clean=violation_list3clean.rename(columns={'businessname':'businessname3'})

#violations with filed only
violation_list1_filed_only=inspection_date_filtered_filed_only.loc[inspection_date_filtered_filed_only['viollevel']=='*'].groupby(["businessname", "licenseno", "viollevel"]).size().reset_index(name="violations 1") #lists occurances of each violation level for each restaurant
violation_list2_filed_only=inspection_date_filtered_filed_only.loc[inspection_date_filtered_filed_only['viollevel']=='**'].groupby(["businessname","licenseno", "viollevel"]).size().reset_index(name="violations 2")
violation_list3_filed_only=inspection_date_filtered_filed_only.loc[inspection_date_filtered_filed_only['viollevel']=='***'].groupby(["businessname","licenseno", "viollevel"]).size().reset_index(name="violations 3")

violation_list1clean_filed_only=violation_list1_filed_only.drop(columns=['viollevel'])
violation_list2clean_filed_only=violation_list2_filed_only.drop(columns=['viollevel'])
violation_list3clean_filed_only=violation_list3_filed_only.drop(columns=['viollevel'])

violation_list1clean_filed_only=violation_list1clean_filed_only.rename(columns={'businessname':'businessname1'})
violation_list2clean_filed_only=violation_list2clean_filed_only.rename(columns={'businessname':'businessname2'})
violation_list3clean_filed_only=violation_list3clean_filed_only.rename(columns={'businessname':'businessname3'})

violation_list3clean_filed_only.head(10) #usually only 1 or 2 filed ones exist
violation_list3clean.head(5) #almost all restaurants have violations, but most don't get filed

businessname3  licenseno  violations 3
0  100 Percent Delicias Express     351943             2
1                149 Eat Street      28288             1
2     20TH CENTRY BOWLING LANES      18671             1
3              21 ST. AMENDMENT      19863             1
4                    224 BOSTON     370784             1

In [33]:
inspection_list.head() #this is the dataframe that we will be adding information to in order to map

businessname  licenseno licstatus           city state  \
0        100 Percent Delicia Food      87059    Active     Roslindale    MA   
71      20TH CENTRY BOWLING LANES      18671    Active      Hyde Park    MA   
161  100 Percent Delicias Express     351943    Active  Jamaica Plain    MA   
199                149 Eat Street      28288    Active   Charlestown/    MA   
209        11 Dining - 1St. Floor     413545    Active         Boston    MA   

                     address_zip       lat         long  
0     635   Hyde Park AVE, 02131  42.27859   -71.119440  
71   1231   Hyde Park AVE, 02136  42.25682   -71.124110  
161       656   Centre ST, 02130  42.31283   -71.113860  
199      300   CHELSEA ST, 02129   42.3732      -71.059  
209     200   Berkeley ST, 02116  42.35006   -71.072919

The following code applies the number of violations for each type to each of the restaurants with the same license number.  Merged_list is all violations, and merged_list_filed_only is only the "filed" violations, which again aren't used for this since it wasn't very usefule (practically nothing filed).  This is set up to look at and read across the rows to ensure the business names are lined up correctly.  I used the merged_list for this with all violations.

In [34]:
merged_list=[]
merged_list=inspection_list.merge(violation_list1clean, on='licenseno', how='left')
merged_list=merged_list.merge(violation_list2clean, on='licenseno', how='left')
merged_list=merged_list.merge(violation_list3clean, on='licenseno', how='left')
#merged_list.head(100)  #make sure to check this for the business names to line up across columns.

merged_list_filed_only=[]
merged_list_filed_only=inspection_list.merge(violation_list1clean_filed_only, on='licenseno', how='left')
merged_list_filed_only=merged_list_filed_only.merge(violation_list2clean_filed_only, on='licenseno', how='left')
merged_list_filed_only=merged_list_filed_only.merge(violation_list3clean_filed_only, on='licenseno', how='left')

#merged_list_filed_only#.head(100)  #make sure to check this for the business names to line up across columns.
merged_list.head(5) #int out either of the last two.  Filed only is the ones that count agains the score, and the merged list is all violations, even if they were corrected


businessname  licenseno licstatus           city state  \
0      100 Percent Delicia Food      87059    Active     Roslindale    MA   
1     20TH CENTRY BOWLING LANES      18671    Active      Hyde Park    MA   
2  100 Percent Delicias Express     351943    Active  Jamaica Plain    MA   
3                149 Eat Street      28288    Active   Charlestown/    MA   
4        11 Dining - 1St. Floor     413545    Active         Boston    MA   

                   address_zip       lat         long  \
0   635   Hyde Park AVE, 02131  42.27859   -71.119440   
1  1231   Hyde Park AVE, 02136  42.25682   -71.124110   
2       656   Centre ST, 02130  42.31283   -71.113860   
3      300   CHELSEA ST, 02129   42.3732      -71.059   
4     200   Berkeley ST, 02116  42.35006   -71.072919   

                  businessname1  violations 1              businessname2  \
0      100 Percent Delicia Food           1.0                        NaN   
1     20TH CENTRY BOWLING LANES           2.0  20TH CENTRY BOWLING LANES   
2  100 Percent Delicias Express           2.0                        NaN   
3                149 Eat Street           1.0                        NaN   
4                           NaN           NaN     11 Dining - 1St. Floor   

   violations 2                 businessname3  violations 3  
0           NaN                           NaN           NaN  
1           1.0     20TH CENTRY BOWLING LANES           1.0  
2           NaN  100 Percent Delicias Express           2.0  
3           NaN                149 Eat Street           1.0  
4           1.0                           NaN           NaN

The following cell creates a score column for each of the establishments from the number of violations and calls the new.  The score methodolgy should be close to what the city of Boston uses, but since we are using all violations, we are only applying a 50% weighting to the penalties. So the level 1 (*) violations are a 0.5 point penalty, the level 2 (**) are a 3.5 point penalty, and the level 3 (***) are a 5 point penalty

In [35]:
active_violation_list=merged_list.drop(columns=['businessname1','businessname2','businessname3']) #drops businessnames after they have been checked
active_violation_list['violations 1']=active_violation_list['violations 1'].replace(np.nan, 0) #replaces null values in violations with integers to calculate score
active_violation_list['violations 2']=active_violation_list['violations 2'].replace(np.nan, 0)
active_violation_list['violations 3']=active_violation_list['violations 3'].replace(np.nan, 0)
active_violation_list['hiddenscore']=100-.5*active_violation_list['violations 1']-3.5*active_violation_list['violations 2']-5*active_violation_list['violations 3'] #This used a 50% weighting from the "filed" scores
#active_violation_list


active_violation_list_filed_only=merged_list_filed_only.drop(columns=['businessname1','businessname2','businessname3']) #drops businessnames after they have been checked
active_violation_list_filed_only['violations 1']=active_violation_list_filed_only['violations 1'].replace(np.nan, 0) #replaces null values in violations with integers to calculate score
active_violation_list_filed_only['violations 2']=active_violation_list_filed_only['violations 2'].replace(np.nan, 0)
active_violation_list_filed_only['violations 3']=active_violation_list_filed_only['violations 3'].replace(np.nan, 0)
active_violation_list_filed_only['publishedscore']=100-1*active_violation_list_filed_only['violations 1']-5*active_violation_list_filed_only['violations 2']-10*active_violation_list_filed_only['violations 3'] #these should be close to what boston uses to grade restaurants

#active_violation_list_filed_only.head(100)   <-use this to look at individual violations
#active_violation_list.head(100)    <-use this to look at individual violations

restaurant_scores=active_violation_list.copy()
restaurant_scores['publishedscore']=active_violation_list_filed_only['publishedscore'].copy()
restaurant_scores.drop(columns=['violations 1', 'violations 2', 'violations 3'], inplace=True)
restaurant_scores.head(5)  #hidden score is a score that takes into account all the warnings that were issued during an inspection at 50% grade, where the published is the graded score.  A large delta between these indicates restaurants are very reactive any may not alway be clean.

businessname  licenseno licstatus           city state  \
0      100 Percent Delicia Food      87059    Active     Roslindale    MA   
1     20TH CENTRY BOWLING LANES      18671    Active      Hyde Park    MA   
2  100 Percent Delicias Express     351943    Active  Jamaica Plain    MA   
3                149 Eat Street      28288    Active   Charlestown/    MA   
4        11 Dining - 1St. Floor     413545    Active         Boston    MA   

                   address_zip       lat         long  hiddenscore  \
0   635   Hyde Park AVE, 02131  42.27859   -71.119440         99.5   
1  1231   Hyde Park AVE, 02136  42.25682   -71.124110         90.5   
2       656   Centre ST, 02130  42.31283   -71.113860         89.0   
3      300   CHELSEA ST, 02129   42.3732      -71.059         94.5   
4     200   Berkeley ST, 02116  42.35006   -71.072919         96.5   

   publishedscore  
0            99.0  
1            99.0  
2           100.0  
3           100.0  
4           100.0

In [36]:
restaurant_scores.sort_values(by='publishedscore') #this is just a list of all restaurants sorted by score

businessname  licenseno licstatus  \
1139                       Ginger Exchange      80677    Active   
2523       Stop & Shop Supermarket No. 075      26027    Active   
1985                    Peet's Coffee Shop      67824    Active   
1701                           Midway Cafe      18278    Active   
761                              Dash Cafe      79181    Active   
385                Brassica Kitchen & Cafe     139236    Active   
1801            Morgan Lewis & Bockius LLP      29909    Active   
2681            The Best Sausage Co.  Inc.      21196    Active   
527                           Casa Razbora      74564    Active   
1703                       MAX'S DELI CAFE      19490    Active   
1822  Museum of Fine Arts Bravo Restaurant      19405    Active   
1856                     OMNI PARKER HOUSE      18954    Active   
2549         Suffolk University Law School      26048    Active   
1060                             Five Guys     386187    Active   
220                        Bani Restaurant      23642    Active   
2746                       The Porter Cafe      74816    Active   
821                 Dona Habana Restaurant     201338    Active   
3042                        Zaz Restaurant      80873    Active   
1749                          MILK ST CAFE      18815    Active   
2314                        Silver Slipper      22525    Active   
2176               Ristorante Toscano Inc.      18300    Active   
132                              AQUITAINE      20803    Active   
928                      Eataly 1St. Floor     163952    Active   
156                          Arizona B B Q      29252    Active   
2471                 STARBUCKS COFFEE INC.      26068    Active   
1096             Four Seasons Hotel Boston      18140    Active   
2665                            Thaitation      31976    Active   
163                Athan's European Bakery      24028    Active   
2234                             Salty Pig      75013    Active   
256    Bella Luna Restaurant @ the Brewery      31331    Active   
...                                    ...        ...       ...   
1450                      KING AND I CORP.      18988    Active   
1451                                   KFC      77640    Active   
1453       Kikka @ Whole Foods Charlestown      92576    Active   
1454         KIKKA @ WHOLE FOODS INK BLOCK     138059    Active   
1455                    Kimchipapi Kitchen     351778    Active   
1456                            Kim's Tofu     201466    Active   
1458                    Kings Bowl Seaport     316908    Active   
411                        Brothers Market     407432    Active   
1460                  Kingston Grill & Bar     201848    Active   
1443                   Kelly's Liquor Mart      19109    Active   
1462                         Kneeland Cafe     418998    Active   
416                            Cafe Presto     308963    Active   
1440                      Kava Neo Taverna     166849    Active   
1425                   Juice and Jazz Cafe     330114    Active   
1426                          Juicy Greens     341751    Active   
1427                            Juicy Spot     201042    Active   
1428                            Jump On In     353620    Active   
1429                   Kaba African Market      27956    Active   
1430                        K Town Chicken      77113    Active   
423                             Bruins Bar     364900    Active   
1432                       Kaju Tofu House      77920    Active   
1433                        KALIHARI GRILL      23768    Active   
421       BRUEGGER'S BAGEL BAKERY No.  274      26153    Active   
1435                                KANTIN      22228    Active   
420                    CHARLESTOWN LIQUORS      21854    Active   
1437                             KMB(TEST)     129226   Deleted   
419                            Burger King      78074    Active   
418                       CAFE PORTO BELLO      20251    Active   
417       

In [37]:
df=inspection_date_filtered[inspection_date_filtered['licenseno']==128432]
#df  #print if you want to look at individual restaurant score from the list above if you want to see whats up.

In [38]:
restaurant_scores.head(5)


businessname  licenseno licstatus           city state  \
0      100 Percent Delicia Food      87059    Active     Roslindale    MA   
1     20TH CENTRY BOWLING LANES      18671    Active      Hyde Park    MA   
2  100 Percent Delicias Express     351943    Active  Jamaica Plain    MA   
3                149 Eat Street      28288    Active   Charlestown/    MA   
4        11 Dining - 1St. Floor     413545    Active         Boston    MA   

                   address_zip       lat         long  hiddenscore  \
0   635   Hyde Park AVE, 02131  42.27859   -71.119440         99.5   
1  1231   Hyde Park AVE, 02136  42.25682   -71.124110         90.5   
2       656   Centre ST, 02130  42.31283   -71.113860         89.0   
3      300   CHELSEA ST, 02129   42.3732      -71.059         94.5   
4     200   Berkeley ST, 02116  42.35006   -71.072919         96.5   

   publishedscore  
0            99.0  
1            99.0  
2           100.0  
3           100.0  
4           100.0

In [39]:
CLIENT_ID = 'QCLOQTK3WRLR4IDGCOF2SWYP2JD2DKVGNQUB1WLBSWWMH4GY' # your Foursquare ID
CLIENT_SECRET = 'IEGKT2SRAZMJWGS2OTOM2U4OESQLHGFTDHFNAR2PAF4NHY0M' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

intent = 'match'
limit = 1 
radius = 100

from pandas.io.json import json_normalize

restaurant_scores['foursquare_id']=0
restaurant_scores['foursquare_likes']=0

Your credentails:
CLIENT_ID: QCLOQTK3WRLR4IDGCOF2SWYP2JD2DKVGNQUB1WLBSWWMH4GY
CLIENT_SECRET:IEGKT2SRAZMJWGS2OTOM2U4OESQLHGFTDHFNAR2PAF4NHY0M


In [40]:
def getFoursquareVenues(names, latitudes, longitudes, radius=100):

    url = 'https://api.foursquare.com/v2/venues/search?&client_id={}&client_secret={}&v={}&query={}&ll={},{}&intent={}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        names,
        latitudes,
        longitudes, 
        intent,
        radius, 
        limit)
            
        # make the GET request
    results = requests.get(url).json()["response"]
    try:
        fs_id = results['venues'][0]['id']
    except IndexError:  #many of the lat long and business names result in an error with foursquare.  If the entry can't find a business ID with the same lat long and name, a 0 is placed in the id field.
        fs_id = 1 #1 means an error came up in the id field

    
    return(fs_id)

In [43]:

for row_index, row in restaurant_scores.iterrows():
    if row['foursquare_id']==0: #if the code stops, can rerun again without looking at the ones we've gotten id's for already
        foursqr_id=getFoursquareVenues(names=row['businessname'],latitudes=row['lat'],longitudes=row['long'])
        print(row['businessname'], "id is", foursqr_id)
        restaurant_scores.loc[row_index,['foursquare_id']]=foursqr_id          
restaurant_scores.head(10)

El Palmar Restaurant id is 1
El Pelon id is 4b9a4e19f964a52006ab35e3
EL PENOL RESTAURANT id is 1
El Pilon id is 1
El Primo Market id is 1
El Recreo Coffee & Roastene id is 54e366c6498e89ccb3519bb4
El Regreso Market id is 1
El Triunfo Restaurant / Ali Baba id is 578e5617498e01b85d660bd2
ELEMENT SEAPORT HOTEL BOSTON id is 569837f3498efe9f1b307b10
ELEMENTS CAFE & CONFERENCE id is 4c7e97d4d860b60ca4625e9d
Elenas Cafe id is 1
Elephant & Castle Pub and Restaurant id is 40b28c80f964a520bcf71ee3
ELLA'S GAS id is 51e9b073498e0c1a470d8d43
EMC CLUB id is 4bcb476efb84c9b6437c1e3e
Embassy Suites @Logan Airport id is 585922cf44587f78dd102b91
Embassy Suites @Logan Airport. id is 585922cf44587f78dd102b91
Flik International @ Merck & Co. id is 4b682660f964a5204d692be3
EMC Inseat id is 4bcb476efb84c9b6437c1e3e
Emmanuel College id is 4be8bcbf4485d13a751594ee
Emirates Lounge id is 511b7a2fe4b091eb63fce0f5
Emmanuel College (Muddy River Cafe) id is 4cc090c9b6c4224b48e1f994
Emmanuel Convenience Market id is 

businessname  licenseno licstatus           city state  \
0      100 Percent Delicia Food      87059    Active     Roslindale    MA   
1     20TH CENTRY BOWLING LANES      18671    Active      Hyde Park    MA   
2  100 Percent Delicias Express     351943    Active  Jamaica Plain    MA   
3                149 Eat Street      28288    Active   Charlestown/    MA   
4        11 Dining - 1St. Floor     413545    Active         Boston    MA   
5                     110 Grill     381384    Active     Dorchester    MA   
6     125 Nashua St. Cafe (MGH)     130844    Active         Boston    MA   
7          129 Lake Street Cafe      74211    Active      Brighton/    MA   
8       163 Vietnamese Sandwich      27609    Active         BOSTON    MA   
9                       Accents      23222    Active    East Boston         

                   address_zip       lat         long  hiddenscore  \
0   635   Hyde Park AVE, 02131  42.27859   -71.119440         99.5   
1  1231   Hyde Park AVE, 02136  42.25682   -71.124110         90.5   
2       656   Centre ST, 02130  42.31283   -71.113860         89.0   
3      300   CHELSEA ST, 02129   42.3732      -71.059         94.5   
4     200   Berkeley ST, 02116  42.35006   -71.072919         96.5   
5     25  Jan Karski Wy, 02125   42.3248     -71.0613        100.0   
6        125  Nashua St, 02114  42.36783   -71.064950         96.5   
7         127   LAKE ST, 02135   42.3449     -71.1637        100.0   
8     66    Harrison AV, 02111   42.3513     -71.0611        100.0   
9          1   Hotel DR, 02128   42.3674     -71.0228        100.0   

   publishedscore             foursquare_id  foursquare_likes  
0            99.0  513b7cbce4b02357defb0f49                 0  
1            99.0  4a62196df964a5201ac31fe3                 0  
2           100.0  5c4e3851dab4b1002c48145c                 0  
3           100.0                         1                 0  
4           100.0                         1                 0  
5           100.0  5d56cf06127e2f0008997d61                 0  
6           100.0  5624f127498e6e0ede7a594c                 0  
7           100.0  4ea016a2490120ec7d4523f8                 0  
8           100.0  4a932354f964a520e81e20e3                 0  
9           100.0                         1                 0

In [44]:
def getFoursquareVenueLikes(venue_id):

    url = 'https://api.foursquare.com/v2/venues/{}/likes?&client_id={}&client_secret={}&v={}'.format(
        venue_id,
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION)    
    
    results = requests.get(url).json()
    try:
        venue_likes = results['response']['likes']['count']
    except IndexError:  #if there are any errors, a 1 is placed in the id field.
        venue_likes = 1 
    return(venue_likes) 

In [45]:
for row_index, row in restaurant_scores.iterrows():
    if row['foursquare_id'] != (0 or 1): #if there is a 0 or 1 here, no ID is there to get likes with
        if row['foursquare_likes'] == 0: #this is so if the command is re-run, it doesn't look up places we have likes for already
            FS_likes=getFoursquareVenueLikes(venue_id=row['foursquare_id'])
            print(row['businessname'], "likes are", FS_likes)
            restaurant_scores.loc[row_index,['foursquare_likes']]=FS_likes
        else:
            pass
restaurant_scores.head(10)

100 Percent Delicia Food likes are 4
20TH CENTRY BOWLING LANES likes are 39
100 Percent Delicias Express likes are 0
110 Grill likes are 0
125 Nashua St. Cafe (MGH) likes are 5
129 Lake Street Cafe likes are 0
163 Vietnamese Sandwich likes are 47
21 ST. AMENDMENT likes are 112
320 Cafe likes are 1
224 BOSTON likes are 38
2Twenty2 likes are 1
49 Social likes are 33
ABIGAIL'S TEA ROOM @CONGRESS BRIDGE likes are 6
73 Cafe likes are 2
75 CHESTNUT likes are 92
75 On Liberty Wharf likes are 72
753 South likes are 9
89 Broad Street/Fin Point likes are 1
A & N PIZZA likes are 4
A C Farm Market likes are 0
Abbott's Frozen Custard likes are 25
A Goodmart likes are 0
A K's Take Out & Delivery likes are 2
Abby Lane likes are 102
AC Hotel by Marriott likes are 7
Aceituna likes are 3
Aceituna Grill likes are 24
Achilitos Taqueria likes are 0
ADAMS CONVENIENCE STORE likes are 1
Adams Fish Mkt likes are 0
AFC Sushi @ Emerson College likes are 24
Avana Express Bar likes are 0
AFC SUSHI @SIMMONS COLLEGE

businessname  licenseno licstatus           city state  \
0      100 Percent Delicia Food      87059    Active     Roslindale    MA   
1     20TH CENTRY BOWLING LANES      18671    Active      Hyde Park    MA   
2  100 Percent Delicias Express     351943    Active  Jamaica Plain    MA   
3                149 Eat Street      28288    Active   Charlestown/    MA   
4        11 Dining - 1St. Floor     413545    Active         Boston    MA   
5                     110 Grill     381384    Active     Dorchester    MA   
6     125 Nashua St. Cafe (MGH)     130844    Active         Boston    MA   
7          129 Lake Street Cafe      74211    Active      Brighton/    MA   
8       163 Vietnamese Sandwich      27609    Active         BOSTON    MA   
9                       Accents      23222    Active    East Boston         

                   address_zip       lat         long  hiddenscore  \
0   635   Hyde Park AVE, 02131  42.27859   -71.119440         99.5   
1  1231   Hyde Park AVE, 02136  42.25682   -71.124110         90.5   
2       656   Centre ST, 02130  42.31283   -71.113860         89.0   
3      300   CHELSEA ST, 02129   42.3732      -71.059         94.5   
4     200   Berkeley ST, 02116  42.35006   -71.072919         96.5   
5     25  Jan Karski Wy, 02125   42.3248     -71.0613        100.0   
6        125  Nashua St, 02114  42.36783   -71.064950         96.5   
7         127   LAKE ST, 02135   42.3449     -71.1637        100.0   
8     66    Harrison AV, 02111   42.3513     -71.0611        100.0   
9          1   Hotel DR, 02128   42.3674     -71.0228        100.0   

   publishedscore             foursquare_id  foursquare_likes  
0            99.0  513b7cbce4b02357defb0f49                 4  
1            99.0  4a62196df964a5201ac31fe3                39  
2           100.0  5c4e3851dab4b1002c48145c                 0  
3           100.0                         1                 0  
4           100.0                         1                 0  
5           100.0  5d56cf06127e2f0008997d61                 0  
6           100.0  5624f127498e6e0ede7a594c                 5  
7           100.0  4ea016a2490120ec7d4523f8                 0  
8           100.0  4a932354f964a520e81e20e3                47  
9           100.0                         1                 0

In [68]:
#restaurant_scores.tail(10)

The following cell is optional but takes a while - it adds all of the violations so they are visible on the map.  Without this, each point is just a color.  With it, you can click on a color and read all of the establishment's violations

In [48]:
restaurant_scores  #(OPTIONAL) run this to add all of the comments from the list in the previous cell to the business name.  This makes all of the comments visible in the map.

for row_index, row in inspection_date_filtered.iterrows():
    
    license = row['licenseno']
    
    for subrow_index, subrow in restaurant_scores.iterrows():
        if subrow['licenseno']==license:
            restaurant_scores.loc[subrow_index,['businessname']]=subrow['businessname']+","+row['violdttm']+'-'+row['comments']
            
restaurant_scores.head(10)

businessname  licenseno licstatus  \
0  100 Percent Delicia Food,2019-05-20 09:04:54-r...      87059    Active   
1  20TH CENTRY BOWLING LANES,2019-10-08 12:05:12-...      18671    Active   
2  100 Percent Delicias Express,2019-05-07 14:57:...     351943    Active   
3  149 Eat Street,2019-04-25 13:48:43-The items o...      28288    Active   
4  11 Dining - 1St. Floor,2019-12-19 11:15:13-rep...     413545    Active   
5                                          110 Grill     381384    Active   
6  125 Nashua St. Cafe (MGH),2019-07-01 11:46:38-...     130844    Active   
7                               129 Lake Street Cafe      74211    Active   
8                            163 Vietnamese Sandwich      27609    Active   
9                                            Accents      23222    Active   

            city state                  address_zip       lat         long  \
0     Roslindale    MA   635   Hyde Park AVE, 02131  42.27859   -71.119440   
1      Hyde Park    MA  1231   Hyde Park AVE, 02136  42.25682   -71.124110   
2  Jamaica Plain    MA       656   Centre ST, 02130  42.31283   -71.113860   
3   Charlestown/    MA      300   CHELSEA ST, 02129   42.3732      -71.059   
4         Boston    MA     200   Berkeley ST, 02116  42.35006   -71.072919   
5     Dorchester    MA     25  Jan Karski Wy, 02125   42.3248     -71.0613   
6         Boston    MA        125  Nashua St, 02114  42.36783   -71.064950   
7      Brighton/    MA         127   LAKE ST, 02135   42.3449     -71.1637   
8         BOSTON    MA     66    Harrison AV, 02111   42.3513     -71.0611   
9    East Boston                1   Hotel DR, 02128   42.3674     -71.0228   

   hiddenscore  publishedscore             foursquare_id  foursquare_likes  
0         99.5            99.0  513b7cbce4b02357defb0f49                 4  
1         90.5            99.0  4a62196df964a5201ac31fe3                39  
2         89.0           100.0  5c4e3851dab4b1002c48145c                 0  
3         94.5           100.0                         1                 0  
4         96.5           100.0                         1                 0  
5        100.0           100.0  5d56cf06127e2f0008997d61                 0  
6         96.5           100.0  5624f127498e6e0ede7a594c                 5  
7        100.0           100.0  4ea016a2490120ec7d4523f8                 0  
8        100.0           100.0  4a932354f964a520e81e20e3                47  
9        100.0           100.0                         1                 0

In [66]:
restaurant_scores.tail(10)

businessname  licenseno licstatus  \
3040  ZELMA LACEY HOUSE,2019-07-29 12:11:23-The hood...      23360    Active   
3041                                            Yvonnes     143281    Active   
3042  Zaz Restaurant,2019-05-07 09:56:08-provide pro...      80873    Active   
3043  Zen Restaurant,2019-12-10 12:15:25-Soils and d...     380313    Active   
3044  ZESTO'S PIZZA,2019-05-21 08:19:51-Cover all op...      75590    Active   
3045                                                 Zo      33151    Active   
3046  Zia Gianna Italian Bakery & Caffe,2019-08-13 1...     350090    Active   
3047  Ziggy's Coffee Bar,2019-04-19 11:16:57- ,2019-...     154404    Active   
3048                                  Zisis Convenience      81039    Active   
3049  Zuma Restaurant,2019-05-07 12:48:03-provide pr...     355979    Active   

               city state                  address_zip        lat       long  \
3040    Charlestown    Ma    9   West School ST, 02129  42.376263 -71.066250   
3041         Boston    MA         3   Winter PL, 02108  42.355420 -71.061469   
3042      Hyde Park    MA       1230   River ST, 02136  42.255780 -71.122989   
3043         Boston    MA        21   Beacon ST, 02108  42.445821 -71.049765   
3044  Jamaica Plain    MA       460   Centre ST, 02130  42.319350 -71.111540   
3045         BOSTON    MA    3   CENTER PLAZA  , 02109  42.293292 -71.063941   
3046     Dorchester    MA  1739  Dorchester AVE, 02124  42.290846 -71.062989   
3047         Boston    MA      100   Tremont ST, 02108  42.357140 -71.060857   
3048       Brighton    MA   375   Washington ST, 02135  42.349310 -71.154199   
3049         Boston    MA          1  Dalton ST, 02115  42.345698 -71.084020   

      hiddenscore  publishedscore             foursquare_id  foursquare_likes  
3040         99.5           100.0  4b563a81f964a5205e0628e3                 1  
3041        100.0           100.0  560d8c06498e79986a22ca43               341  
3042         47.0            95.0  50897d79e4b00b147d875792                 5  
3043         69.5           100.0                         1                 0  
3044         74.0           100.0  4ae20f84f964a520518a21e3                 4  
3045        100.0           100.0                         1                 0  
3046         97.5           100.0  5aad17a759c42315a14e8c64                 4  
3047         98.0            96.0  57407fb2498e4398968539dd                18  
3048        100.0           100.0  4cab73d176d3a0938e562c6b                 0  
3049         86.5            99.0  5ce9e86e3731ee002b84d1cc                12

The following code just makes sure that the lat longs are numbers and not strings which makes folium have an error

In [65]:
restaurant_scores['lat']= restaurant_scores['lat'].astype(float)
restaurant_scores['long']= restaurant_scores['long'].astype(float) #converts lat and long strings to numbers

The following block creates the folium map of boston with establishements plotted.  The colors range from green to red based on the past-year food inspection violations.  The size of the points are based on FourSquare likes.  Establishements with a large amount of likes have a larger circle, and those with a smaller amount of likes have a smaller circle.  Establishements that did not get data from the FourSquare database are a med-small size for default.  The outer ring of each establishment represents the filed or "reinspected" score, of which at the time of this, all passed.  If it were red, the filed violations should have been high enough to suspend the license of the site.

In [69]:
# create map of Boston using latitude and longitude values
map_boston = folium.Map(width="100%", height="100%", location=[42.361145, -71.05083], zoom_start=12) #tiles= 'Stamen Terrain'


# add markers to map

def marker_fills(hidden_score):
    if hidden_score>92:
        return 'green'
    elif hidden_score>84:
        return 'greenyellow'
    elif hidden_score>76:
        return 'yellow'
    elif hidden_score>68:
        return 'orange'
    elif hidden_score>60:
        return 'darkorange'
    else:
        return 'red'
    

def border_fills(published_score):
    if published_score>90:
        return 'green'
    else:
        return 'red'    
    
def radius_size(likes):
    if likes >600:
        return 14
    elif likes >400:
        return 13
    elif likes >200:
        return 12
    elif likes >150:
        return 11    
    elif likes >100:
        return 10
    elif likes >80:
        return 9
    elif likes >40:
        return 8
    elif likes >20:
        return 7
    elif likes >10:
        return 6
    elif likes >5:
        return 5
    elif likes >1:
        return 4
    else:
        return 6 # for establishments with 0 likes (which may be due to error, a default value of 6 is provided for size)

for lat, lng, businessname, hidden_score, published_score, likes  in zip(restaurant_scores['lat'], restaurant_scores['long'], restaurant_scores['businessname'], restaurant_scores['hiddenscore'], restaurant_scores['publishedscore'], restaurant_scores['foursquare_likes']):
    label = '{}'.format(businessname)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=radius_size(likes),
        popup=label,
        color=border_fills(published_score), #'blue',
        fill=True,
        fill_color=marker_fills(hidden_score),  #'#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_boston)  
 
map_boston

